In [1]:
from IPython import get_ipython
%load_ext autoreload
%autoreload 2

In [2]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'
# InteractiveShell.ast_node_interactivity = "last_expr"
import sys
import os

sys.path.insert(0, '/nas/xd/projects/transformers/src')
os.environ['HF_HOME'] = '/raid/xd/.cache/torch'
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
# os.environ["CUDA_VISIBLE_DEVICES"]="7"

from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from types import MethodType
from tqdm import tqdm
from collections import defaultdict, OrderedDict, Counter
from datetime import datetime
from io import StringIO
from itertools import chain
import math
from functools import reduce
import numpy as np 
%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sns

import random
import torch
import torch.nn as nn
import torch.nn.functional as F 
from torch.utils.data.sampler import RandomSampler, Sampler, SequentialSampler
from torch.utils.data.dataloader import DataLoader

from transformers.data.data_collator import DataCollator, default_data_collator
from transformers import AutoConfig, pipeline
from transformers import RobertaForMaskedLM, RobertaTokenizer, GPT2LMHeadModel, GPT2Tokenizer, GPTNeoForCausalLM, AutoModelForCausalLM

from transformers import GPT2LMHeadModel, GPT2Tokenizer, GPTNeoForCausalLM, GPTJForCausalLM
import pysvelte as ps 
import unseal
import string
from itertools import product, chain
import math
import json
from IPython.display import HTML, display

import torch
from unseal import transformers_util as tutil
from unseal import hooks
import unseal.visuals.utils as utils
from unseal.hooks import HookedModel
import copy
from math import log, exp

from utils import *
# from child_utils import *
from common_utils import *
# from model_utils import *
from weight_analysis import *

In file_utils.py: default_cache_path = /raid/xd/.cache/torch/hub


In [3]:
from utils_nrk import *
import pandas as pd
import matplotlib.pyplot as plt

# 载入模型

In [4]:
models = {}
cache_dir = '/nas/xd/.cache/torch/transformers/'  # for models besides t5-3b/11b
# cache_dir = '/mnt/nvme1/xd/.cache/torch/transformers/'  # for gpt-j-6B on elderberry

proxies = {'http': '192.168.50.1:1081'} 
model_name = "EleutherAI/gpt-j-6B"
# device = torch.device('cpu')
device = torch.device('cuda:7')
# model = GPTJForCausalLM.from_pretrained(model_name, proxies=proxies, cache_dir=cache_dir)
# model_name = "EleutherAI/gpt-neo-1.3B"
model = GPTJForCausalLM.from_pretrained(model_name, proxies=proxies, cache_dir=cache_dir,revision="float16", torch_dtype=torch.float16, low_cpu_mem_usage=True).to(device)
# model = AutoModelForCausalLM.from_pretrained(model_name, proxies=proxies, cache_dir=cache_dir)
tokenizer = GPT2Tokenizer.from_pretrained('gpt2', cache_dir=cache_dir)
models[model_name] = model, tokenizer

In [5]:
head_list = load_list("head_list",1)
text,pos = find_position(tokenizer, head_list, 0)
Data = make(model, tokenizer, text, pos, 0, device, "dot")
# print(Data)

In [29]:
# head_list = load_list("head_list","1")
heads = [(5,12), (7,9) , (7,2) , (6,5) , (3,7) , (8,7) , (6,2) , (3,12)]


# matrix,heads = Constructing_probability_matrix(tokenizer,data[num], heads, pos)
# draw_prob(tokenizer, data1[num][0], heads, matrix)

{(5, 12): [(16, 13)], (7, 9): [], (7, 2): [(16, 13), (19, 13)], (6, 5): [(4, 1), (11, 4), (19, 18), (12, 6), (15, 13)], (3, 7): [], (8, 7): [(16, 13), (17, 13), (19, 18)], (6, 2): [(16, 13)], (3, 12): [(16, 14), (12, 7), (17, 14), (11, 6), (10, 6)]}
length: 21 
 token: [464, 3623, 373, 407, 48090, 503, 286, 262, 6873, 475, 503, 286, 262, 31489, 780, 262, 31489, 318, 13044, 88, 13]


(16, 13)

(16, 13)

(16, 13)

(16, 13)

(12, 7)

(11, 6)

In [5]:
head_list = load_list("head_list",1)
data = []
for i in tqdm(range(len(head_list))):
    text,pos = find_position(tokenizer, head_list, i)
    Data = make(model, tokenizer, text, pos, i, device, "dot")
    data.append(Data)
        
dump_list(data,"probability_dot_all",int(1))

100%|██████████| 1267/1267 [14:50<00:00,  1.42it/s]


In [30]:
data1 = load_list("probability_dot_all",1)
data_head, sorted_list = sort_prob_diff(data1, (8,7))
show_difference_of_probability(sorted_list)

文本编号  token位置  token_id  是否预测正确  清除注意力前概率  清除注意力后概率    log概率差  \
0     1091       15     34183       1  0.992411  0.059794 -2.809228   
1     1085       14     34183       1  0.992537  0.100626 -2.288852   
2      855       20        13       1  0.482654  0.051122 -2.245087   
3      184       16      5889       1  0.991234  0.173771 -1.741211   
4      321       15     33515       1  0.428855  0.101429 -1.441756   
5      322       15     33515       1  0.428855  0.101429 -1.441756   
6      844       21     34183       1  0.991727  0.242960 -1.406550   
7      516       16     34183       1  0.998151  0.294443 -1.220818   
8      896       14      1074       1  0.639699  0.189243 -1.217965   
9      642       17     33577       1  0.989156  0.310783 -1.157758   
10    1124       20      3201       1  0.982058  0.317626 -1.128774   
11     863       22     33577       1  0.995559  0.324347 -1.121489   
12    1028       19      1664       1  0.672303  0.230957 -1.068477   
13     720       17       373       1  0.267613  0.092326 -1.064219   
14     158       17     33577       1  0.993143  0.354852 -1.029175   
15    1047       17      1097       1  0.669703  0.240975 -1.022143   
16     825       29     21857       1  0.981899  0.373286 -0.967143   
17     683       14      5166       1  0.605170  0.236255 -0.940599   
18    1020       17      2000       1  0.701574  0.278497 -0.923920   
19     171       24        77       1  0.878955  0.363250 -0.883643   
20    1095       28       340       1  0.872895  0.383766 -0.821782   
21     876       16      3775       1  0.988057  0.437269 -0.815191   
22     368       12       319       1  0.663812  0.301160 -0.790356   
23    1027       18       373       1  0.461337  0.219931 -0.740816   
24     214       23        13       1  0.406613  0.195090 -0.734402   
25     793       19       607       1  0.519643  0.249643 -0.733111   
26     767       15     48311       1  0.980498  0.472723 -0.729552   
27     424       13       319       1  0.517461  0.249489 -0.729520   
28    1190       15      1660       1  0.276778  0.135962 -0.710840   
29     951       12       262       1  0.810544  0.400783 -0.704285   
30     885       15      4190       1  0.281691  0.139846 -0.700267   
31    1074       20       373       1  0.589904  0.295457 -0.691437   
32    1200       17      4105       1  0.891718  0.448221 -0.687863   
33     762       18      1842       1  0.539945  0.275479 -0.672955   
34    1115       17       345       1  0.383867  0.196275 -0.670780   
35     988       14       318       1  0.279774  0.144425 -0.661226   
36      96       14     11694       1  0.179366  0.093375 -0.652805   
37     721       17       373       1  0.222775  0.116390 -0.649213   
38    1237       15      4483       1  0.331036  0.177687 -0.622202   
39    1221       17        13       1  0.461411  0.248126 -0.620354   
40     860       22     30853       1  0.993994  0.534715 -0.619997   
41     317       19        13       1  0.404672  0.219090 -0.613595   
42    1167       22       373       1  0.442673  0.241217 -0.607137   
43     860       29       318       1  0.461146  0.251379 -0.606753   
44     203       18       257       1  0.281790  0.155500 -0.594517   
45     211       13       373       1  0.356665  0.197034 -0.593420   
46     737       19     33577       1  0.996358  0.551959 -0.590632   
47     881       14       373       1  0.070289  0.039413 -0.578504   
48     578       20      2635       1  0.956098  0.536283 -0.578198   
49    1049       19      5379       1  0.834872  0.470424 -0.573644   
50    1021       25       373       1  0.442531  0.249421 -0.573369   
51     579       20      5961       1  0.960866  0.545530 -0.566077   
52    1057       21       606       1  0.423552  0.242365 -0.558232   
53     653       22       373       1  0.438245  0.252301 -0.552157   
54     132       23      1999       1  0.999627  0.576877 -0.549753   
55     710       29      4255 

In [5]:
data1 = load_list("probability_dot_without_same",1)
data_head, sorted_list = sort_prob_diff(data1, (8,7))
show_difference_of_probability(sorted_list)

文本编号  token位置  token_id  是否预测正确  清除注意力前概率  清除注意力后概率    log概率差  \
0     1091       15     34183       1  0.992516  0.060003 -2.805850   
1     1085       14     34183       1  0.992544  0.100710 -2.288022   
2      418       15     34183       1  0.993315  0.143369 -1.935627   
3      184       16      5889       1  0.991312  0.173303 -1.743989   
4      321       15     33515       1  0.429169  0.101433 -1.442455   
5      322       15     33515       1  0.429169  0.101433 -1.442455   
6      844       21     34183       1  0.991734  0.243437 -1.404597   
7      516       16     34183       1  0.998176  0.294735 -1.219854   
8      896       14      1074       1  0.639064  0.189062 -1.217931   
9      642       17     33577       1  0.989139  0.309796 -1.160919   
10    1124       20      3201       1  0.981718  0.318061 -1.127061   
11     863       22     33577       1  0.995654  0.325147 -1.119123   
12     158       17     33577       1  0.993088  0.354535 -1.030013   
13     825       29     21857       1  0.981811  0.371631 -0.971499   
14     683       14      5166       1  0.605520  0.236204 -0.941390   
15     171       24        77       1  0.879008  0.362595 -0.885506   
16    1095       28       340       1  0.874641  0.383069 -0.825598   
17     876       16      3775       1  0.987892  0.436975 -0.815697   
18     368       12       319       1  0.667149  0.301165 -0.795355   
19     767       15     48311       1  0.980507  0.472442 -0.730154   
20    1190       15      1660       1  0.276533  0.135978 -0.709837   
21    1200       17      4105       1  0.891714  0.448159 -0.687998   
22    1115       17       345       1  0.383619  0.196027 -0.671398   
23     762       18      1842       1  0.539934  0.278460 -0.662171   
24    1221       17        13       1  0.464252  0.248115 -0.626534   
25     860       22     30853       1  0.993994  0.531539 -0.625954   
26     737       19     33577       1  0.996285  0.548172 -0.597445   
27     578       20      2635       1  0.956112  0.536727 -0.577385   
28    1049       19      5379       1  0.834912  0.470439 -0.573660   
29     579       20      5961       1  0.960261  0.545391 -0.565703   
30     710       29      4255       1  0.938507  0.541451 -0.550038   
31     132       23      1999       1  0.999630  0.576967 -0.549600   
32      61       15       651       1  0.150885  0.091157 -0.503935   
33     307       14       407       1  0.883663  0.535337 -0.501179   
34    1220       21      3763       1  0.235524  0.145803 -0.479556   
35    1149       21     18701       1  0.999404  0.625597 -0.468452   
36     902       19      5509       1  0.362124  0.227176 -0.466260   
37     595       18       588       1  0.351989  0.220844 -0.466146   
38     660       20       319       1  0.586104  0.370416 -0.458872   
39     661       20       319       1  0.586104  0.370416 -0.458872   
40     711       27       284       1  0.500561  0.319906 -0.447702   
41    1104       16      7962       1  0.340048  0.220599 -0.432742   
42     213       23        13       1  0.484981  0.317124 -0.424818   
43    1005       20       496       1  0.983038  0.650738 -0.412540   
44      61       17       262       1  0.546830  0.364146 -0.406584   
45     370        8       351       1  0.389339  0.261821 -0.396787   
46    1094       16      2342       1  0.303572  0.205683 -0.389283   
47    1060       14       262       1  0.581277  0.395765 -0.384407   
48     315       17      3249       1  0.119976  0.082032 -0.380184   
49    1166       25       330       1  0.967276  0.664225 -0.375863   
50       5       22      4870       1  0.678340  0.466703 -0.373955   
51     387       16       340       1  0.745199  0.514830 -0.369814   
52     236       17       262       1  0.636052  0.441685 -0.364683   
53    1067       16     34144       1  0.973907  0.677796 -0.362470   
54     780       21        13       1  0.431089  0.300088 -0.362240   
55     383       28       372 

In [6]:
data1 = load_list("probability_dot_only_same",1)
data_head, sorted_list = sort_prob_diff(data1, (8,7))
show_difference_of_probability(sorted_list)

文本编号  token位置  token_id  是否预测正确  清除注意力前概率  清除注意力后概率    log概率差  \
0      855       20        13       1  0.483212  0.051106 -2.246554   
1      642       17     33577       1  0.989139  0.309796 -1.160919   
2      863       22     33577       1  0.995654  0.325147 -1.119123   
3     1028       19      1664       1  0.671514  0.230889 -1.067597   
4      720       17       373       1  0.268207  0.092823 -1.061069   
5     1047       17      1097       1  0.666660  0.240637 -1.018991   
6      683       14      5166       1  0.605520  0.236204 -0.941390   
7     1020       17      2000       1  0.703937  0.278600 -0.926911   
8     1095       28       340       1  0.874641  0.383069 -0.825598   
9     1027       18       373       1  0.461156  0.220231 -0.739058   
10     793       19       607       1  0.519631  0.249100 -0.735266   
11     214       23        13       1  0.406517  0.195397 -0.732594   
12     424       13       319       1  0.513701  0.248659 -0.725560   
13     885       15      4190       1  0.283002  0.139666 -0.706198   
14     951       12       262       1  0.808840  0.400397 -0.703146   
15    1074       20       373       1  0.589955  0.295674 -0.690790   
16     988       14       318       1  0.279579  0.143214 -0.668941   
17     721       17       373       1  0.223859  0.116363 -0.654300   
18    1237       15      4483       1  0.331789  0.178464 -0.620112   
19     860       29       318       1  0.461018  0.251579 -0.605680   
20    1167       22       373       1  0.442229  0.242564 -0.600565   
21     203       18       257       1  0.281552  0.155170 -0.595794   
22     211       13       373       1  0.356228  0.197670 -0.588973   
23     881       14       373       1  0.070223  0.039214 -0.582644   
24     578       20      2635       1  0.956112  0.536727 -0.577385   
25    1021       25       373       1  0.442574  0.250997 -0.567166   
26    1057       21       606       1  0.423630  0.242431 -0.558145   
27     653       22       373       1  0.437617  0.252023 -0.551824   
28     132       23      1999       1  0.999630  0.576967 -0.549600   
29    1194       19       318       1  0.363577  0.211600 -0.541293   
30    1057       20       787       1  0.408497  0.238380 -0.538620   
31     565       17       423       1  0.216489  0.127788 -0.527166   
32      42       26       561       1  0.499221  0.295362 -0.524846   
33    1020       16        82       1  0.793082  0.478642 -0.504974   
34     893       16      1064       1  0.260406  0.158510 -0.496426   
35     939       19     46908       1  0.177760  0.109524 -0.484293   
36    1220       21      3763       1  0.235524  0.145803 -0.479556   
37      48       13      2085       1  0.183673  0.114309 -0.474251   
38     902       19      5509       1  0.362124  0.227176 -0.466260   
39     719       25       547       1  0.473363  0.297770 -0.463541   
40     356       19      5321       1  0.810946  0.512742 -0.458429   
41      95       13       373       1  0.605586  0.387564 -0.446316   
42      21       17       373       1  0.307029  0.197873 -0.439318   
43     313       19       373       1  0.232460  0.150383 -0.435536   
44     325       10       645       1  0.174554  0.112925 -0.435511   
45      70       20        88       1  0.976092  0.636627 -0.427373   
46     451       22      1165       1  0.274870  0.179645 -0.425313   
47     213       23        13       1  0.484981  0.317124 -0.424818   
48    1005       20       496       1  0.983038  0.650738 -0.412540   
49     178       18       736       1  0.699883  0.463913 -0.411215   
50    1068       16       373       1  0.407098  0.270799 -0.407677   
51     286       18      1097       1  0.124377  0.082861 -0.406158   
52     435       17      5166       1  0.681767  0.454436 -0.405632   
53     420       15       550       1  0.284853  0.190012 -0.404884   
54    1185       12       477       1  0.701339  0.469219 -0.401922   
55     991       19       547 

In [74]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "last_expr" 
head_list = load_list("head_list",1)

num = 855
head = (8,7)
token = 13

text,pos = find_position(tokenizer, head_list, num)
print(pos)
Text = tokenizer.encode(text)
print("length:",len(Text),"\n","token:",Text)

for i in pos.items():
    Pos = i[1]  
    for j in Pos:
        if(Text[j[0]] == Text[j[1]] or j[0]-j[1]==1):
            Pos.pop(Pos.index(j))
            
print(pos)
print(text)
for i in pos[head]:
    print(f"{i[0]}_{tokenizer.convert_ids_to_tokens(Text[i[0]])}—>{i[1]}_{tokenizer.convert_ids_to_tokens(Text[i[1]])}")


print(tokenizer.convert_ids_to_tokens(token))

{(5, 12): [(16, 13)], (7, 9): [], (7, 2): [(16, 13), (19, 13)], (6, 5): [(4, 1), (11, 4), (19, 18), (12, 6), (15, 13)], (3, 7): [], (8, 7): [(16, 13), (17, 13), (19, 18)], (6, 2): [(16, 13)], (3, 12): [(16, 14), (12, 7), (17, 14), (11, 6), (10, 6)]}
length: 21 
 token: [464, 3623, 373, 407, 48090, 503, 286, 262, 6873, 475, 503, 286, 262, 31489, 780, 262, 31489, 318, 13044, 88, 13]
{(5, 12): [], (7, 9): [], (7, 2): [(19, 13)], (6, 5): [(4, 1), (11, 4), (12, 6), (15, 13)], (3, 7): [], (8, 7): [(17, 13)], (6, 2): [], (3, 12): [(16, 14), (17, 14), (10, 6)]}
The gas was not smelling out of the tank but out of the hose because the hose is leaky.
17_Ġis—>13_Ġhose
20_.
.


In [73]:
print(head_list[0])
a = tokenizer.encode(head_list[0][0])
print(a)
print(a[9],a[7],a[5])

['Sarah was a much better surgeon than Maria so Maria always got the easier cases.', {(5, 12): [[[9, 7], [14200, 14200], 0.2961062490940094]], (7, 9): [[[9, 6], [14200, 621], 0.6641659140586853]], (7, 2): [], (6, 5): [[[14, 5], [2663, 23923], 0.8733249306678772], [[12, 5], [262, 23923], 0.5251620411872864]], (3, 7): [[[14, 5], [2663, 23923], 0.662680447101593]], (8, 7): [[[9, 7], [14200, 14200], 0.9720789790153503]], (6, 2): [[[9, 7], [14200, 14200], 0.953004777431488]], (3, 12): [[[9, 8], [14200, 523], 0.5409765839576721]]}]
[29284, 373, 257, 881, 1365, 23923, 621, 14200, 523, 14200, 1464, 1392, 262, 4577, 2663, 13]
14200 14200 23923


In [78]:
for num in ["1"]:
    head_list = load_list("head_list",num)
    data = []
    for i in tqdm(range(len(head_list))):
        text,pos = find_position(tokenizer, head_list, i)
        a = tokenizer.encode(text)
        Pos = copy.deepcopy(pos)
        for j in Pos.items():
            Pos1 = j[1]
            for k in Pos1:
                if(a[k[0]] != a[k[1]]):
                    num = pos[j[0]].index(k)
                    pos[j[0]].pop(num)   
                    
        Data = make(model, tokenizer, text, pos, i, device, "dot")
        data.append(Data)

    dump_list(data,"probability_dot_only_same",int(num))

100%|██████████| 1267/1267 [06:00<00:00,  3.51it/s]


In [53]:
for num in ["1"]:
    head_list = load_list("head_list",num)
    data = []
    for i in tqdm(range(len(head_list))):
        text,pos = find_position(tokenizer, head_list, i)
        a = tokenizer.encode(text)
        Pos = copy.deepcopy(pos)
        for j in Pos.items():
            Pos1 = j[1]
            for k in Pos1:
                if(a[k[0]] == a[k[1]]):
                    num = pos[j[0]].index(k)
                    pos[j[0]].pop(num)   
                    
        Data = make(model, tokenizer, text, pos, i, device, "dot")
        data.append(Data)

    dump_list(data,"probability_dot_without_same",int(num))

KeyError: 1

In [ ]:
tokenizer.convert_ids_to_tokens(13)

In [9]:
# data2 = load_list("probability_dot",1)
data_head, sorted_list = sort_prob_diff(data2, (8,7))
show_difference_of_probability(sorted_list)

文本编号  token位置  token_id  是否预测正确  清除注意力前概率  清除注意力后概率    log概率差  \
0      230       21      8365       1  0.376126  0.277962 -0.302439   
1      457       18      6891       1  0.252206  0.193556 -0.264676   
2      368       12       319       1  0.663812  0.519789 -0.244576   
3      359       16     18221       1  0.320211  0.255830 -0.224468   
4       96       14     11694       1  0.179366  0.155555 -0.142428   
5      653       22       373       1  0.438245  0.383104 -0.134471   
6      892       13       319       1  0.570748  0.504811 -0.122763   
7      730       17      6125       1  0.100322  0.088734 -0.122749   
8     1142       14       373       1  0.280688  0.250963 -0.111941   
9      649       22      4197       1  0.221408  0.198632 -0.108553   
10     650       22      4197       1  0.221408  0.198632 -0.108553   
11    1136       15      2746       1  0.103085  0.092707 -0.106106   
12       5       22      4870       1  0.678306  0.615118 -0.097784   
13    1215       18      2248       1  0.123687  0.112465 -0.095113   
14     845       12       257       1  0.502457  0.457603 -0.093508   
15    1094       18      3195       1  0.250530  0.228180 -0.093443   
16     713       27       373       1  0.376500  0.343196 -0.092617   
17     245       22       307       1  0.129636  0.118187 -0.092460   
18     399       17        13       1  0.213588  0.194754 -0.092312   
19    1190       15      1660       1  0.276778  0.252414 -0.092143   
20     683       14      5166       1  0.605170  0.552762 -0.090581   
21     762       17       287       1  0.084379  0.077207 -0.088828   
22     482       23       373       1  0.455162  0.417223 -0.087033   
23     762       18      1842       1  0.539945  0.495657 -0.085584   
24      70       18       373       1  0.268250  0.246271 -0.085488   
25     876       21      2952       1  0.211020  0.194107 -0.083543   
26     615        5       714       1  0.166462  0.153596 -0.080441   
27     456       16       547       1  0.257106  0.237800 -0.078055   
28    1065       12       373       1  0.141630  0.131196 -0.076529   
29     327       17       263       1  0.365438  0.338659 -0.076102   
30     749       20        13       1  0.216893  0.201159 -0.075312   
31     325       10       645       1  0.174588  0.162184 -0.073696   
32     699       16      1865       1  0.345535  0.320991 -0.073680   
33      48       13      2085       1  0.184932  0.171830 -0.073483   
34     513       24      4465       1  0.239756  0.222848 -0.073132   
35    1004       21       329       1  0.634495  0.590158 -0.072438   
36     949       21     21693       1  0.612718  0.569943 -0.072367   
37    1252       15      1402       1  0.489501  0.455744 -0.071455   
38     347       17      8887       1  0.087873  0.081842 -0.071111   
39     988       14       318       1  0.279774  0.261171 -0.068809   
40     215       21      6491       1  0.277702  0.259561 -0.067556   
41     571       16       373       1  0.578516  0.540813 -0.067393   
42     830       13       319       1  0.372204  0.347977 -0.067305   
43      51       20      1165       1  0.283350  0.264981 -0.067028   
44    1094       18      3195       1  0.250530  0.234604 -0.065678   
45     683       15        13       1  0.246867  0.231309 -0.065093   
46     137       19      4494       1  0.354524  0.332327 -0.064656   
47     199       11       683       1  0.500543  0.469236 -0.064589   
48     712       15        13       1  0.406691  0.381811 -0.063127   
49     925       14       262       1  0.298118  0.280043 -0.062548   
50     938       16       257       1  0.165982  0.155960 -0.062277   
51     201       15      1637       1  0.141013  0.132551 -0.061880   
52    1243       15      1748       1  0.330871  0.311039 -0.061808   
53     893       16      1064       1  0.260316  0.244733 -0.061731   
54     595       18       588       1  0.352249  0.331303 -0.061303   
55     765       23       373 

In [40]:
data3 = load_list("probability",1) #row
data_head, sorted_list = sort_prob_diff(data3, (8,7))
show_difference_of_probability(sorted_list)

文本编号  token位置  token_id  是否预测正确  清除注意力前概率  清除注意力后概率    log概率差  \
0      368       12       319       1  0.663812  0.477183 -0.330098   
1      457       18      6891       1  0.252206  0.198055 -0.241702   
2      359       16     18221       1  0.320211  0.252817 -0.236315   
3      230       21      8365       1  0.376126  0.305044 -0.209471   
4      762       18      1842       1  0.539945  0.460004 -0.160232   
5     1190       15      1660       1  0.276778  0.236233 -0.158393   
6      482       23       373       1  0.455162  0.389131 -0.156739   
7      699       16      1865       1  0.345535  0.297979 -0.148073   
8      327       17       263       1  0.365438  0.316846 -0.142680   
9       96       14     11694       1  0.179366  0.155956 -0.139855   
10     762       17       287       1  0.084379  0.073562 -0.137183   
11    1004       21       329       1  0.634495  0.556550 -0.131072   
12     649       22      4197       1  0.221408  0.195200 -0.125984   
13     650       22      4197       1  0.221408  0.195200 -0.125984   
14     653       22       373       1  0.438245  0.389325 -0.118363   
15     730       17      6125       1  0.100322  0.089352 -0.115809   
16     876       21      2952       1  0.211020  0.188165 -0.114632   
17    1136       15      2746       1  0.103085  0.092048 -0.113240   
18    1215       18      2248       1  0.123687  0.110549 -0.112293   
19     414       21       373       1  0.134968  0.120715 -0.111604   
20     245       22       307       1  0.129636  0.116473 -0.107064   
21    1089       16       607       1  0.480150  0.431843 -0.106035   
22     286       18      1097       1  0.123422  0.111006 -0.106027   
23     814       10       284       1  0.260328  0.234195 -0.105792   
24     535       21      3024       1  0.219294  0.197789 -0.103212   
25     325       10       645       1  0.174588  0.157718 -0.101616   
26    1058       22      3436       1  0.194567  0.176442 -0.097785   
27    1018       15       373       1  0.177552  0.161231 -0.096423   
28     896       21     26088       1  0.309614  0.281349 -0.095730   
29       5       22      4870       1  0.678306  0.617189 -0.094422   
30    1004       21       329       1  0.634495  0.577508 -0.094107   
31       5       22      4870       1  0.678306  0.619066 -0.091387   
32     595       18       588       1  0.352249  0.321750 -0.090563   
33     141       17        13       1  0.217547  0.198838 -0.089924   
34    1129       15      1165       1  0.221833  0.202821 -0.089600   
35     289       20       286       1  0.446096  0.408080 -0.089071   
36     749       20        13       1  0.216893  0.198753 -0.087344   
37     609       18     14595       1  0.398779  0.365528 -0.087065   
38     721       17       373       1  0.222775  0.204222 -0.086956   
39    1252       15      1402       1  0.489501  0.449045 -0.086262   
40     988       14       318       1  0.279774  0.256811 -0.085642   
41     845       12       257       1  0.502457  0.461420 -0.085203   
42     892       13       319       1  0.570748  0.524142 -0.085186   
43    1142       14       373       1  0.280688  0.258137 -0.083754   
44     863       15       340       1  0.309186  0.284348 -0.083744   
45     864       15       340       1  0.309186  0.284348 -0.083744   
46     893       16      1064       1  0.260316  0.239429 -0.083640   
47    1094       18      3195       1  0.250530  0.230437 -0.083600   
48      13       25      4043       1  0.614908  0.566125 -0.082657   
49     571       16       373       1  0.578516  0.533715 -0.080604   
50     521       25      4259       1  0.414128  0.382667 -0.079011   
51     199       11       683       1  0.500543  0.462667 -0.078687   
52    1038       16      1972       1  0.246864  0.228221 -0.078520   
53     672       10       257       1  0.322719  0.298439 -0.078219   
54     669       18      4276       1  0.457910  0.423787 -0.077440   
55     958       16       307 

In [49]:
# heads = [(5,12), (7,9) , (7,2) , (6,5) , (3,7) , (8,7) , (6,2) , (3,12)]
# data_head = Filter_head(data1, (3,12))[0]
# data_head

In [16]:
tokenizer.convert_ids_to_tokens(13)

'.'

In [64]:
head_list = load_list("head_list","1")
heads = [(5,12), (7,9) , (7,2) , (6,5) , (3,7) , (8,7) , (6,2) , (3,12)]
num = 230
text,pos = find_position(tokenizer, head_list, num)

matrix,heads = Constructing_probability_matrix(tokenizer,data1[num], heads, pos)
draw_prob(tokenizer, data1[num][0], heads, matrix)

# show_activation(model, tokenizer, head_list, heads, 1091)

In [167]:
out.logits[0, 2].softmax(-1)[318]
out.logits[0, -4].softmax(-1)[318]

tensor(0.9436, grad_fn=<SelectBackward0>)

tensor(0.9436, grad_fn=<SelectBackward0>)

In [179]:
out.logits[0].argmax(1)
out.logits[0].argmax(1)[2:]

tensor([2506, 1438,  318,  198,  290,  314])

tensor([318, 198, 290, 314])

In [97]:
tokenizer.convert_ids_to_tokens([2506, 1438,  318,  198,  290,  314])

['Ġeveryone', 'Ġname', 'Ġis', 'Ċ', 'Ġand', 'ĠI']

# 运行流程

# 运行部分

In [11]:
# heads = [(5,12), (7,9) , (7,2) , (6,5) , (3,7) , (8,7) , (6,2) , (3,12)]
# head_list = load_list("head_list","4")
# rate = show_rate(head_list, heads)
# rate

In [16]:
# distance = show_loc(head_list, (3,12), tokenizer) #取最大的概率值的关注位置
# distance

In [79]:
tokenizer.encode('\nFelicia')

[198, 42493, 33577]

In [41]:
which_sentence(head_list,1085)
a = tokenizer.encode('\nFelicia experienced a tummy ache while Tanya did not because Tanya had not eaten any food.')
tokenizer.convert_ids_to_tokens(a[10])
tokenizer.convert_ids_to_tokens(a[13])
tokenizer.convert_ids_to_tokens(a[14])

Tanya recently finished filling out a job application but not Megan because Tanya is currently unemployed.


'anya'

'Ġbecause'

'ĠT'

In [14]:
#show_times_distence(head_list, [(6,5)],tokenizer)

In [19]:
# import random
# import einops
# heads = [(5,12), (7,9) , (7,2) , (6,5) , (3,7) , (8,7) , (6,2) , (3,12)]
    
# head_list = load_list("head_list","1")
# show_activation(model, tokenizer, head_list, heads, 1091)
# # show_activations(model, tokenizer, head_list, heads, 952)

In [21]:
import npm
from contextlib import suppress
from typing import Optional
import random
import pysvelte as ps 
heads = [(5, 12), (7, 9)]

texts = read_texts("4")
head_dict = find_activations(model, tokenizer, texts, heads)
dump_dict(head_dict)
head_dict = load_dict()
show_activations(model, tokenizer, head_dict, heads, 952)

In [42]:
text = "Avery was debating on taking up German instead of Latin, because the Latin was old."
sent = tokenizer.tokenize(text)

In [52]:
tokenized_text = list(map(tokenizer.convert_tokens_to_string, map(lambda x: x, sent))) 
print(tokenized_text)

['A', 'very', ' was', ' debating', ' on', ' taking', ' up', ' German', ' instead', ' of', ' Latin', ',', ' because', ' the', ' Latin', ' was', ' old', '.']


In [51]:
a = list(map(lambda x: x, sent))
print(a)

['A', 'very', 'Ġwas', 'Ġdebating', 'Ġon', 'Ġtaking', 'Ġup', 'ĠGerman', 'Ġinstead', 'Ġof', 'ĠLatin', ',', 'Ġbecause', 'Ġthe', 'ĠLatin', 'Ġwas', 'Ġold', '.']


In [6]:
# x = torch.randn(5, 5) #随机生成一个二维Tensor
# x = x[2:].detach().numpy()
# x1 = x
# x1 = torch.tensor(x1)
# print(x1)
# for i,j in enumerate(x1):
#     print("Max",max(j))
#     a = torch.squeeze((j==torch.max(j)).nonzero(),0)
#     if(a[0]!=0):
#         b = int(a[0])
#         c = (i,b)
#         print(type(c[0]))
#         print(j)
#         print(j[int(a[0])])
# print(x[a[0]][a[1]])

In [ ]:
import re
text = ['white -> black',
'big -> small',
'ask -> answer',
'permit -> forbid',
'attack -> defend',
'bring -> take',
'buy -> sell',
'start -> end',
'believe -> doubt',
'blame -> praise',
'come -> go',
'cry -> laugh',
'cure -> hurt',
'die -> live',
'divide -> unite',
'earn -> spend',
'fail -> succeed',
'fall -> rise ',
'forget -> remember',
'forgive -> punish',
'gain -> loss',
'glance -> stare']

device = torch.device('cpu')
# def mask_ans(Text):
#     Text[-1] = re.findall(r'[\w.%+-]+.+\>\B', Text[-1])[0]
#     return ", ".join(Text)

# texts = []
# for i in range(10):
#     Text = random.choices(text,k=3)
#     texts.append(mask_ans(Text))

def pred_right(model, Data, input_ids, out):
    data = copy.deepcopy(Data)
    for i in range(len(data)):
        data[i]["prob_2"] = None
    data[-1]["prob_2"] = out.logits[0, -2].softmax(-1)[input_ids[0][-1]].item()
            
    for i in range(len(data)):
        data[i]["Prob_diff"] = 0
        
    for i in range(0,len(data)):
        if data[i]["prob_2"] != None:
            data[i]["Prob_diff"] = log(data[i]["prob_2"]) - log(data[i]["prob_1"])
            
    data1 = []        
    for i in data:
        if i["Prob_diff"] != 0:
            data1.append(i)
    return data1

def make(model,tokenizer, text, pos, num, device, heads):
    inputs = tokenizer.encode_plus(text, return_tensors='pt')
    inputs = prepare_inputs(inputs, device)
    Data = []
    json_dict = {}
    data ={}
    #前传第一次，不清除注意力
    out = model(**inputs, output_attentions=True)
    
    data["sentence"] = num
    data["pos"] = 0
    data["token_id"] = tokenizer.convert_ids_to_tokens(inputs.input_ids[0][0].item())
    data["is_right"] = 0
    data["prob_1"] = 0
    Data.append(data) #开头第一个token，不预测
    for i in range(1,len(inputs.input_ids[0])):
        data = {}
        token = inputs.input_ids[0][i].item()
        right = 1 if out.logits[0].argmax(1)[i-1] == token else 0
        prob = out.logits[0, i-1].softmax(-1)[token].item()
        data["sentence"] = num
        data["pos"] = i
        data["token_id"] = tokenizer.convert_ids_to_tokens(token)
        data["is_right"] = right
        data["prob_1"] = prob
        Data.append(data)
        
    #前传第二次，清除注意力
    for i,j in heads:
        data_dict = {}
        layer = i
        head = j
        self = model.transformer.h[layer].attn
        self.mask = create_mask(head, [(2,0),(6,4)], len(inputs.input_ids[0]))
        self.mask = self.mask.to(device)
        out = model(**inputs, output_attentions=True)
        data = pred_right(model, Data, inputs.input_ids, out)
        json_dict[(layer,head)] = data
        del self.mask
        del self
    return [text,json_dict]

def show_difference_of_probability(data):
    difference = pd.DataFrame(data, columns = ["文本编号","token位置", "token_id", "是否预测正确","清除注意力前概率","清除注意力后概率","log概率差"])   
    pd.set_option('display.max_rows', None)      
    return difference

def sort_prob_diff(data, head):
    data_head = Filter_head(data, head)[0]
    data_head_dict = []
    for i in data_head:
        print(i.values())
        for k in list(i.values())[:]:
            data_head_dict.append(k)
    print(data_head_dict)
    data_head = sorted(data_head_dict, key=lambda x:x['Prob_diff'])
    
    sorted_list = [list(i.values())[:] for i in data_head if list(i.values())[-2] > 1e-2 or list(i.values())[-2] < -1e-2]
    
    return data_head, sorted_list
# heads = [(5,12), (7,9) , (7,2) , (6,5) , (3,7) , (8,7) , (6,2) , (3,12), (4,8)]
# # head_list = find_activations(model, tokenizer, texts, heads)
# # dump_list(head_list,"Antonym",0)
# head_list = load_list("Antonym",0)
# data = []
# for i in tqdm(range(len(head_list))):
#     text,pos = find_position(tokenizer, head_list, i)
#     Data = make(model, tokenizer, text, [], i, device, heads)
#     data.append(Data)
    
# data_head, sorted_list = sort_prob_diff(data, (7,9))
# show_difference_of_probability(sorted_list)
    
# dump_list(data,"Antonym_probability",0)
# data_head = Filter_head(data, (7,9))
# print(data_head)

data1 = load_list("Antonym_probability",0)
data_head, sorted_list = sort_prob_diff(data1, (7,9))
show_difference_of_probability(sorted_list)